Testing data positive feedback dynamic (20%)


In [1]:
import os
import pandas as pd
import numpy as np
import random
import time
import tensorflow as tf

In [2]:
def relu(x):
    return np.maximum(0,x)  

def softmax(x):
    exp_x = np.exp(x)
    softmax_x = exp_x / np.sum(exp_x)
    return softmax_x 

def sigmoid(z):
    return 1 / (1 + np.exp(-z))

In [3]:
user_following = np.load('../Data/npy/user_following_1489.npy')[:100]
all_3374 = np.load('../Data/npy/all_3374D.npy')
user_category = np.load('../Data/npy/user_category_1489.npy')[:100]
YouTuber_category = np.load('../Data/npy/YouTuber_category_0.7.npy')
active_users = np.load('../Data/npy/active_userID_1489.npy')[:100]

In [4]:
#The number of followers for each YouTuber
YouTuber_followers = np.sum(user_following, axis=0)
print(YouTuber_followers)
over5 = 0
for num in YouTuber_followers:
    if num >= 5:
        over5+=1
print('The num of followers over 5:',over5)

[ 8  0  2 24  1  0  0 11 47  7 25 32 10  1 16  1  6 24  3  2  1  6  4  0
 39 39 10 16 27 22  0  2 17 15  0  2  0  8  2  1 28 16  3 33  9 24  0  3
  0  9  0  0  0  2 28  2  2 18  0  3 23  0  2 39  0  1  1 65  0  2 18 21
  7  1 47 14 19  1  3 66  3  0 28  3 20  0  6  0]
The num of followers over 5: 42


In [5]:
print('user_following shape ',user_following.shape)
print('all_3374 shape ',all_3374.shape)
print('user_category shape ',user_category.shape)
print('YouTuber_category shape ',YouTuber_category.shape)

user_following shape  (100, 88)
all_3374 shape  (88, 3374)
user_category shape  (100, 17)
YouTuber_category shape  (88, 17)


In [6]:
user_category_norm = np.zeros(user_category.shape)
for i in range(len(user_category)):
    user_category_norm[i] = user_category[i]/np.max(user_category[i])
print('user_category after normalized by max...')
print('user_category_norm shape ',user_category_norm.shape)

user_category after normalized by max...
user_category_norm shape  (100, 17)


In [7]:
following_true = [0]*len(user_following)
for i in range(len(user_following)):
    each_user = []
    for j in range(len(user_following[i])):
        if user_following[i][j] == 1:
            each_user.append(j)
    following_true[i] = each_user
#print(following_true)

In [8]:
#最少跟最多的following 
minlen = 10000
maxlen = 0
num_of_follower = []
for i in range(len(following_true)):
    if len(following_true[i]) < minlen:
        minlen = len(following_true[i])
    if len(following_true[i]) > maxlen:
        maxlen = len(following_true[i])
    num_of_follower.append(len(following_true[i]))
print('Min number of followings ',minlen)
print('Max number of followings ',maxlen)

Min number of followings  5
Max number of followings  21


In [9]:
over_10 = 0
over_8 = 0
over_12 = 0
user_idx_over10 = []
avg_over10 = 0
for i in range(len(num_of_follower)):
    num = num_of_follower[i]
    if num >= 10:
        over_10 += 1
        user_idx_over10.append(i)
        avg_over10+=num
    if num >= 8:
        over_8 += 1
    if num >= 12:
        over_12 += 1
print('over 8:',over_8)
print('over 10:',over_10)
print('over 12:',over_12)
print('avg 10:',avg_over10/len(user_idx_over10))

over 8: 68
over 10: 56
over 12: 28
avg 10: 12.517857142857142


In [10]:
len(user_idx_over10)

56

# Training data and Testing data

In [11]:
test_amount = 10
yt_test_amount = 20

In [12]:
#user_idx = [i for i in range(len(user_following))]
user_idx = user_idx_over10
#test_idx is the number of user for testing
test_idx = random.sample(user_idx,test_amount)

In [13]:
# Training  and Testing
train_t = [0]*(len(user_following))
train_f = [0]*(len(user_following))
# Testing 
test_t = [0]*test_amount
test_f = [0]*test_amount
test_pos = -1

for i in range(len(user_following)):
    t_for_train = []
    f_for_train = []
    if i not in test_idx: #if not in test id, just append it to true or false list
        for j in range(88):
            if user_following[i][j] == 1:
                t_for_train.append(j)
            else:
                f_for_train.append(j)
        train_t[i] = t_for_train
        train_f[i] = f_for_train
        
    else: #if in test id, choose 2 true and other 
        test_pos += 1
        temp_t = []
        temp_f = []
        for j in range(88):
            if user_following[i][j] == 1:
                temp_t.append(j)
            else:
                temp_f.append(j)
        # random choose 2 true and 8 false for test 
        if len(temp_t)*0.2 < 1:
            t_for_test = random.sample(temp_t,1)
            f_for_test  = random.sample(temp_f,yt_test_amount-1)
        else:
            if len(temp_t)*0.2 > 5:
                t_num = int(round(float(len(temp_t)*0.2)))
            else:      
                t_num = 5
            #t_num = int(round(float(len(temp_t)*0.2)))
            t_for_test = random.sample(temp_t,t_num)
            f_for_test  = random.sample(temp_f,yt_test_amount-t_num)
        test_t[test_pos] = t_for_test
        test_f[test_pos] = f_for_test
        
        #other for training
        t_for_train = [item for item in temp_t if not item in t_for_test]
        f_for_train = [item for item in temp_f if not item in f_for_test]
        train_t[i] = t_for_train
        train_f[i] = f_for_train

In [14]:
# Training  and Testing --New
train_t = [0]*(len(user_following))
train_f = [0]*(len(user_following))
# Testing 
test_t = [0]*test_amount
test_f = [0]*test_amount
test_pos = -1

for i in range(len(user_following)):
    t_for_train = []
    f_for_train = []
    if i not in test_idx: #if not in test id, just append it to true or false list
        for j in range(88):
            if user_following[i][j] == 1:
                t_for_train.append(j)
            else:
                f_for_train.append(j)
        train_t[i] = t_for_train
        train_f[i] = f_for_train
        
    else: #if in test id, choose 2 true and other 
        test_pos += 1
        temp_t = []
        temp_f = []
        for j in range(88):
            if user_following[i][j] == 1:
                temp_t.append(j)
            else:
                temp_f.append(j)
        print(len(temp_t),round(0.5*len(temp_t)+0.4999999999))
        t_for_test = random.sample(temp_t,round(0.5*len(temp_t)+0.4999999999))
        f_for_test  = random.sample(temp_f,yt_test_amount-len(t_for_test))
        
        test_t[test_pos] = t_for_test
        test_f[test_pos] = f_for_test
        
        #other for training
        t_for_train = [item for item in temp_t if not item in t_for_test]
        print(len(t_for_train ))
        f_for_train = [item for item in temp_f if not item in f_for_test]
        train_t[i] = t_for_train
        train_f[i] = f_for_train

10 5
5
11 6
5
13 7
6
16 8
8
11 6
5
19 10
9
15 8
7
10 5
5
19 10
9
12 6
6


In [15]:
total_test = 0
for t in test_t:
    total_test += len(t)
avg = total_test/test_amount
avg

7.1

In [16]:
# train_t[i] 代表的是user i positive feedback
print('The length of train_t:',len(train_t))
print('The length of train_f:',len(train_t))
print('The length of test_t:',len(test_t))
print('The length of test_f:',len(test_f))

The length of train_t: 100
The length of train_f: 100
The length of test_t: 10
The length of test_f: 10


# Recommendation  Module

In [17]:
"""
n: the number of users
m: the number of YouTubers
k: latent dims
l: feature dims
"""
tf.reset_default_graph()
n = len(user_following)
m = 88  
k = 100
l = 3374

user = tf.placeholder(tf.int32,shape=(1,))
i = tf.placeholder(tf.int32, shape=(1,))
j = tf.placeholder(tf.int32, shape=(1,))

#多少個auxliary 
xf = tf.placeholder(tf.float32, shape=(None,l))
l_id = tf.placeholder(tf.int32, shape=(None,))
l_id_len = tf.placeholder(tf.int32,shape=(1,))
r = tf.placeholder(tf.float32,shape=(None,))


image_i = tf.placeholder(tf.float32, shape=(1,l))
image_j = tf.placeholder(tf.float32, shape=(1,l))

with tf.variable_scope("item_level"):
    user_latent = tf.get_variable("user_latent", [n, k],
                                      initializer=tf.random_normal_initializer(0,0.1,seed=3))
    item_latent = tf.get_variable("item_latent", [m, k],
                                      initializer=tf.random_normal_initializer(0,0.1,seed=3)) 
    aux_item = tf.get_variable("aux_item", [m, k],
                                      initializer=tf.random_normal_initializer(0,0.1,seed=3))
    W1 = tf.get_variable("W1", [n, k],
                                      initializer=tf.contrib.layers.xavier_initializer())
    Wu = tf.get_variable("Wu", [k,k],
                                      initializer=tf.contrib.layers.xavier_initializer())
    Wy = tf.get_variable("Wy", [m,k,k],
                                     initializer=tf.contrib.layers.xavier_initializer())
    Wa = tf.get_variable("Wa", [k,k],
                                     initializer=tf.contrib.layers.xavier_initializer())
    Wv = tf.get_variable("Wv", [k,l],
                                    initializer=tf.contrib.layers.xavier_initializer())
    
    

    aux_new = tf.get_variable("aux_new", [1,k], initializer=tf.constant_initializer(0.0))
    ########## Error part, how to get auxisize dynamically
    ####aux_size= tf.get_variable(name='aux_size', initializer=l_id.get_shape().as_list()[-1])
    
with tf.variable_scope('feature_level'):
    Beta = tf.get_variable("beta", [n,l],
                             # initializer=tf.contrib.layers.xavier_initializer())
                                     initializer=tf.random_normal_initializer(0.00001,0.000001,seed=10))

#lookup the latent factors by user and id
u = tf.nn.embedding_lookup(user_latent, user) #(1*k) 第幾個user latent factor
vi = tf.nn.embedding_lookup(item_latent, i) 
vj = tf.nn.embedding_lookup(item_latent, j)

w1 = tf.nn.embedding_lookup(W1, user) #(1*k)
wu = Wu
#wu = tf.squeeze(tf.nn.embedding_lookup(Wu, user)) #(k*k)
wy = tf.squeeze(tf.nn.embedding_lookup(Wy, i)) #(k*k)
wa = Wa
#wa = tf.squeeze(tf.nn.embedding_lookup(Wa, user)) #(k*k)
wv = Wv
#wv = tf.squeeze(tf.nn.embedding_lookup(Wv, user)) #(k,l)

beta = tf.nn.embedding_lookup(Beta, user) #user feature latent factor


The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



In [18]:
a_list=tf.Variable([])
q = tf.constant(0)
def att_cond(q,a_list):
    return tf.less(q,l_id_len[0])
def att_body(q,a_list):
    xfi = tf.expand_dims(xf[q],0) #(1,l)
    
    a_list = tf.concat([a_list,[(tf.matmul( w1, tf.nn.relu( tf.matmul(wu, u, transpose_b=True) +
        tf.matmul(wy, tf.expand_dims(tf.nn.embedding_lookup(item_latent,l_id[q]),0), transpose_b=True) +
        tf.matmul(wa, tf.expand_dims(tf.nn.embedding_lookup(aux_item, l_id[q]),0), transpose_b=True) +
        tf.matmul(wv, xfi, transpose_b=True)))[0][0])*r[q]]],0)
    q += 1
    return q,  a_list

_, a_list = tf.while_loop(att_cond,att_body,[q,a_list],shape_invariants=[q.get_shape(),tf.TensorShape([None])])

a_list_soft=tf.nn.softmax(a_list)


aux_np = tf.expand_dims(tf.zeros(k),0) #dimension (1,32)
q = tf.constant(0)
def sum_att_cond(q,aux_np):
    return tf.less(q,l_id_len[0])

def sum_att_body(q,aux_np):
    #aux_np+=a_list_soft[q]*tf.expand_dims(tf.nn.embedding_lookup(aux_item, l_id[q]),0)
    aux_np = tf.math.add_n([aux_np,a_list_soft[q]*tf.expand_dims(tf.nn.embedding_lookup(aux_item, l_id[q]),0)]) 
    q += 1
    return q, aux_np

_,aux_np = tf.while_loop(sum_att_cond,sum_att_body,[q,aux_np])

"""
for q in range(3): #取q個auxliary item
    aux_np+=a_list_soft[q]*tf.expand_dims(tf.nn.embedding_lookup(aux_item, l_id[q]),0)
"""

aux_part = tf.matmul(aux_np, vi, transpose_b=True)
#tf.print('aux attention:',aux_np)
aux_np+=u #user_latent factor + sum (alpha*auxilary)
aux_new=tf.assign(aux_new,aux_np) #把aux_new 的 值變成aux_np

bigger_part = tf.matmul(aux_new, vi, transpose_b=True)
big_f_part = tf.matmul(beta,image_i, transpose_b=True)
smaller_part = tf.matmul(aux_new, vj, transpose_b=True)
small_f_part = tf.matmul(beta,image_j, transpose_b=True)
#矩陣中對應函數各自相乘
xui = tf.matmul(aux_new, vi, transpose_b=True)+ tf.matmul(beta,image_i, transpose_b=True)
xuj = tf.matmul(aux_new, vj, transpose_b=True)+ tf.matmul(beta,image_j, transpose_b=True)

xuij = tf.subtract(xui,xuj)

norm_par = [tf.reduce_sum(tf.multiply(u, u)),tf.reduce_sum(tf.multiply(vi, vi)),tf.reduce_sum(tf.multiply(vj, vj)),
           tf.reduce_sum(tf.multiply(w1, w1)),tf.reduce_sum(tf.multiply(wu, wu)),tf.reduce_sum(tf.multiply(wy, wy)),
           tf.reduce_sum(tf.multiply(wa, wa)),tf.reduce_sum(tf.multiply(wv,wv)),tf.reduce_sum(tf.multiply(beta,beta))]
l2_norm = tf.add_n([
            0.0001 * tf.reduce_sum(tf.multiply(u, u)),
            0.0001 * tf.reduce_sum(tf.multiply(vi, vi)),
            0.0001 * tf.reduce_sum(tf.multiply(vj, vj)),
  
            0.001 * tf.reduce_sum(tf.multiply(w1, w1)),
            0.001 * tf.reduce_sum(tf.multiply(wu, wu)),
            0.001 * tf.reduce_sum(tf.multiply(wy, wy)),
            0.001 * tf.reduce_sum(tf.multiply(wa, wa)),
            0.0001 * tf.reduce_sum(tf.multiply(wv,wv)),
            
            0.0001 * tf.reduce_sum(tf.multiply(beta,beta)),
            
          ])

loss = l2_norm -tf.log(tf.sigmoid(xuij)) # objective funtion
train_op = tf.train.AdamOptimizer(learning_rate=0.0001).minimize(loss) #parameter optimize 
auc = tf.reduce_mean(tf.to_float(xuij > 0))

Instructions for updating:
Use `tf.cast` instead.


In [19]:
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
loss_acc_list = []
t0=time.time()

#use_true=init_list_of_objects(136)
#use_test=init_list_of_objects(136)

#train_pair_t=[] #positive feedback
#train_pair_f=[] #negative feedback
train_yes_id=[] 
for q in range(5):
    print('Iteraction:',q)
    train_auc=0
    total_loss=0
    xuij_auc=0
    length = 0
    for z in range(n):
        """
        yes 用來存放選擇到的YouTuber feature (for auxilary)
        yesr 用來存放user對該YouTuber的喜好程度(user_category 跟 YouTuber_category的相似性)
        r_3 用來存放user 對該YouTuber種類的偏好(取max)
        """
        yes=[]
        yesr=[]
        
        
        sample=random.sample(train_t[z],len(train_t[z])) #隨機選3個sample true's YouTuber
        train_yes_id.append(sample) #sample全部丟進去
        
        #sample=random.sample(train_t[z]+train_f[z],len(train_t[z])+len(train_f[z]))
        
        #change
        r_3=np.zeros(len(sample)) 
        alpha_history = []
        a_list_history = []
        U_history = []
        Y_history = []
        
        #print(len(sample))
        #check if all YouTuber are in train_t or train_f
        #if len(train_t[z])+len(train_f[z]) != 88:
            #print(z,len(train_t[z])+len(train_f[z]))
         
        for b in range(len(sample)):
            yes.append(all_3374[sample[b]])
            yesr.append(YouTuber_category[sample[b]]*user_category_norm[z])
            #print('YouTuber_category ', YouTuber_category[sample[k]])
            #print('User_category ',user_category_norm[z])
        #print(yesr)
        
        for b in range(len(yesr)):
            r_3[b]=max(yesr[b])
        #print('r_3:',r_3)
        
        yes=np.array(yes)
        #print('user shape should be ',np.array([z]).shape)
        #print('xf shape should be ',yes.shape)
        #print('r shape should be ',np.array(r_3).shape)
        #print('l_id shape should be ',np.array(sample).shape)
        
        #not_used_list = list(set(train_t[z]).difference(set(sample)))
        
        #取positive 
        train_t_sample = random.sample(train_t[z],len(train_t[z]))
        print('number of positive feedback', len(train_t_sample))
        
        train_f_sample = random.sample(train_f[z],20)
        for ta in train_t_sample:
            #print(ta,'--> positive feedback')
            
            pos = sample.index(ta)
            #new_sample = np.delete(sample,[pos])
            #new_yes = np.delete(yes,[pos],axis=0)
            #new_r_3 = np.delete(r_3,[pos])
            new_sample = sample
            new_yes = yes
            new_r_3 = r_3
            #print(len(yes),len(new_yes))
            #print(yes)
            #print(new_yes)
            
            
            
            #ta=random.choice(train_t[z]) #ta is true positve photo
            #train_pair_t.append(ta)
            image_1=np.expand_dims(all_3374[ta],0) #(1,2048)
            #print('Image_1 shape ',image_1.shape)
            #train_f_sample = random.sample(train_f[z],20)
            print('True:',train_t_sample,'Now:',ta)
            print('False:',train_f_sample)
            for b in train_f_sample:
                #print('likes:',ta,';Not likes:',b)
                #b=random.choice(train_f[z])  #b is no feedback photo
                #train_pair_f.append(b)
                image_2=np.expand_dims(all_3374[b],0) #(1,2048)
                #print('Image_2 shape',image_2.shape)
            
                #use_test[z].append(b)
                _norm_par,_big_f_part,_small_f_part,_smaller_part,_aux_part,_bigger_part,Uu,Yy,_a_list,r3,_auc, _loss,_=sess.run([norm_par,big_f_part,small_f_part,smaller_part,aux_part,bigger_part,user_latent,item_latent,a_list,a_list_soft,auc,loss,train_op], feed_dict={user: [z],
                                        i: [ta], j: [b], xf: new_yes , l_id:new_sample, l_id_len:[len(new_sample)],r:new_r_3,
                                        image_i:image_1,image_j:image_2})
                #print('User latent factor')
                #print(Uu.shape)
                #print(Uu)
                #print('Item latent factor')
                #print(Yy.shape)
                #print(Yy)
                U_history.append(Uu)
                Y_history.append(Yy)
                
                #print(XUIJ)
                #print('loss=',_loss)
                #print('auc=',_auc)
                print('user positive negative',z,ta,b)
                print('u,vi,vj',_norm_par[:3])
                print('w1,wu,wy,wa,wv',_norm_par[3:8])
                print('Beta',_norm_par)
                #print('only _aux_part',_aux_part)
                #print('_bigger_part',_bigger_part)
                #print('_smaller_part',_smaller_part)
                #print('_big_f_part',_big_f_part)
                #print('_small_f_part',_small_f_part)
                
                #print(r3)
                print('alpha list before softmax:',_a_list)
                print('---------------------------------------------------')
                a_list_history.append(_a_list)
                alpha_history.append(r3)
                train_auc+=_auc
                total_loss+=_loss
                length += 1
            #now1+=1
        
        #np.savez('../Data/latent_factor/YRM_up10/'+str(q)+'_'+str(z)+'.npz', User=U_history, YouTuber=Y_history)
    
    #print('mine:',xuij_auc/136)    
    #print('a_list_soft:',r3)
    print("total_loss:-----------------", total_loss/length)
    print("train_auc:-------------------", train_auc/length)
    print('---------------------------------------------------------------------------------------------------')
    loss_acc_list.append([total_loss/length,train_auc/length,time.time()-t0])
    print('time:',time.time()-t0,' sec')
print('Total cost ',time.time()-t0,' sec')       

Iteraction: 0
number of positive feedback 7
True: [16, 44, 15, 24, 13, 29, 37] Now: 16
False: [26, 20, 79, 86, 33, 30, 7, 58, 61, 28, 81, 78, 0, 46, 39, 40, 38, 73, 56, 54]
user positive negative 0 16 26
u,vi,vj [1.1538038, 0.9134294, 0.7529391]
w1,wu,wy,wa,wv [1.0784693, 100.42012, 1.1366224, 99.67137, 194.39232]
Beta [1.1538038, 0.9134294, 0.7529391, 1.0784693, 100.42012, 1.1366224, 99.67137, 194.39232, 3.399217e-07]
alpha list before softmax: [0.5705971  1.6255102  0.74987626 1.5506464  1.6206466  1.5712368
 1.4228088 ]
---------------------------------------------------
user positive negative 0 16 20
u,vi,vj [1.1521194, 0.9134397, 1.1096933]
w1,wu,wy,wa,wv [1.0766556, 100.247086, 1.1185585, 99.4989, 193.08505]
Beta [1.1521194, 0.9134397, 1.1096933, 1.0766556, 100.247086, 1.1185585, 99.4989, 193.08505, 3.261124e-05]
alpha list before softmax: [0.5695138 1.6189462 0.748339  1.5445133 1.613545  1.5649451 1.4177167]
---------------------------------------------------
user positive nega

user positive negative 0 44 46
u,vi,vj [1.0987313, 1.1455256, 1.0277265]
w1,wu,wy,wa,wv [1.0197663, 94.825806, 0.89842546, 94.09563, 152.94891]
Beta [1.0987313, 1.1455256, 1.0277265, 1.0197663, 94.825806, 0.89842546, 94.09563, 152.94891, 0.010008934]
alpha list before softmax: [0.5358087 1.4050806 0.6852332 1.336701  1.383456  1.3753209 1.2439551]
---------------------------------------------------
user positive negative 0 44 39
u,vi,vj [1.0971005, 1.1458197, 1.1375571]
w1,wu,wy,wa,wv [1.0180297, 94.66055, 0.87952775, 93.930954, 151.8102]
Beta [1.0971005, 1.1458197, 1.1375571, 1.0180297, 94.66055, 0.87952775, 93.930954, 151.8102, 0.010511583]
alpha list before softmax: [0.5341083 1.3985279 0.6830406 1.3306115 1.376166  1.3690989 1.2384613]
---------------------------------------------------
user positive negative 0 44 40
u,vi,vj [1.0954721, 1.1461167, 1.0980189]
w1,wu,wy,wa,wv [1.0162959, 94.49558, 0.86082727, 93.76654, 150.67896]
Beta [1.0954721, 1.1461167, 1.0980189, 1.0162959, 94.49

user positive negative 0 24 79
u,vi,vj [1.0524688, 1.1127212, 1.0460377]
w1,wu,wy,wa,wv [0.9704905, 90.14248, 1.1227908, 89.42862, 122.864006]
Beta [1.0524688, 1.1127212, 1.0460377, 0.9704905, 90.14248, 1.1227908, 89.42862, 122.864006, 0.024869489]
alpha list before softmax: [0.47190535 1.2149031  0.6196796  1.1637924  1.1659447  1.2091664
 1.0697511 ]
---------------------------------------------------
user positive negative 0 24 86
u,vi,vj [1.0509115, 1.1130868, 0.8557306]
w1,wu,wy,wa,wv [0.9688313, 89.98497, 1.100745, 89.27168, 121.930145]
Beta [1.0509115, 1.1130868, 0.8557306, 0.9688313, 89.98497, 1.100745, 89.27168, 121.930145, 0.02525359]
alpha list before softmax: [0.47003734 1.2089629  0.6172439  1.1579497  1.1595043  1.2030791
 1.0644569 ]
---------------------------------------------------
user positive negative 0 24 33
u,vi,vj [1.0493568, 1.1134977, 1.3380272]
w1,wu,wy,wa,wv [0.96717465, 89.827736, 1.0766506, 89.115005, 121.002785]
Beta [1.0493568, 1.1134977, 1.3380272, 0.96

user positive negative 0 13 46
u,vi,vj [1.0053279, 1.2414302, 1.0273715]
w1,wu,wy,wa,wv [0.9202578, 85.379944, 0.7786402, 84.68341, 96.75601]
Beta [1.0053279, 1.2414302, 1.0273715, 0.9202578, 85.379944, 0.7786402, 84.68341, 96.75601, 0.036886424]
alpha list before softmax: [0.41679755 1.0444858  0.5441247  0.98972684 0.9981896  1.0233861
 0.92418003]
---------------------------------------------------
user positive negative 0 13 39
u,vi,vj [1.0038453, 1.2424029, 1.1344522]
w1,wu,wy,wa,wv [0.918678, 85.23036, 0.7517421, 84.53439, 96.00519]
Beta [1.0038453, 1.2424029, 1.1344522, 0.918678, 85.23036, 0.7517421, 84.53439, 96.00519, 0.037427265]
alpha list before softmax: [0.414724   1.039152   0.5417313  0.9846226  0.9921626  1.0180267
 0.91933036]
---------------------------------------------------
user positive negative 0 13 40
u,vi,vj [1.0023651, 1.2433765, 1.1002436]
w1,wu,wy,wa,wv [0.9171008, 85.081024, 0.72558403, 84.38561, 95.259674]
Beta [1.0023651, 1.2433765, 1.1002436, 0.9171008, 

user positive negative 0 37 33
u,vi,vj [0.9604265, 0.8654424, 1.3382343]
w1,wu,wy,wa,wv [0.87242866, 80.85598, 1.0488226, 80.17673, 75.796455]
Beta [0.9604265, 0.8654424, 1.3382343, 0.87242866, 80.85598, 1.0488226, 80.17673, 75.796455, 0.053717386]
alpha list before softmax: [0.357151   0.8974498  0.4756697  0.83420354 0.8199955  0.8657562
 0.7857272 ]
---------------------------------------------------
user positive negative 0 37 30
u,vi,vj [0.9590136, 0.8660483, 0.98671556]
w1,wu,wy,wa,wv [0.87092435, 80.71387, 1.0148048, 80.03516, 75.19477]
Beta [0.9590136, 0.8660483, 0.98671556, 0.87092435, 80.71387, 1.0148048, 80.03516, 75.19477, 0.054322153]
alpha list before softmax: [0.3554052  0.8928558  0.47339946 0.8295666  0.8148335  0.861226
 0.78129834]
---------------------------------------------------
user positive negative 0 37 7
u,vi,vj [0.95760286, 0.8666876, 0.9693494]
w1,wu,wy,wa,wv [0.86942255, 80.57198, 0.9799691, 79.89383, 74.59741]
Beta [0.95760286, 0.8666876, 0.9693494, 0.869

...

user positive negative 41 27 62
u,vi,vj [0.45218948, 1.3819155, 1.0373588]
w1,wu,wy,wa,wv [0.4793319, 0.0, 0.00030947322, 0.0, 0.0]
Beta [0.45218948, 1.3819155, 1.0373588, 0.4793319, 0.0, 0.00030947322, 0.0, 0.0, 0.39508963]
alpha list before softmax: [1.2067111e-04 2.4911019e-06 2.9166999e-05 3.2999094e-05 4.9858850e-06
 1.3977614e-06]
---------------------------------------------------
user positive negative 41 27 61
u,vi,vj [0.44980037, 1.3826189, 0.90308493]
w1,wu,wy,wa,wv [0.47648582, 0.0, 0.0001136393, 0.0, 0.0]
Beta [0.44980037, 1.3826189, 0.90308493, 0.47648582, 0.0, 0.0001136393, 0.0, 0.0, 0.39749736]
alpha list before softmax: [8.3806102e-05 3.8885546e-06 1.7112174e-05 2.0761590e-05 1.3614236e-06
 1.8052679e-06]
---------------------------------------------------
user positive negative 41 27 83
u,vi,vj [0.44743413, 1.3837664, 1.0594516]
w1,wu,wy,wa,wv [0.4736673, 0.0, 4.3313754e-05, 0.0, 0.0]
Beta [0.44743413, 1.3837664, 1.0594516, 0.4736673, 0.0, 4.3313754e-05, 0.0, 0.0, 0.3

user positive negative 42 14 36
u,vi,vj [1.0057067, 0.9250986, 0.88292557]
w1,wu,wy,wa,wv [0.8545197, 0.0, 7.248709e-05, 0.0, 0.0]
Beta [1.0057067, 0.9250986, 0.88292557, 0.8545197, 0.0, 7.248709e-05, 0.0, 0.0, 0.044492476]
alpha list before softmax: [ 2.0587882e-05 -1.2345232e-06 -3.7585683e-06  5.0989215e-06
  3.2399013e-05  1.2761341e-04 -2.2583805e-05 -8.2761617e-06
  1.9054016e-05  3.6506608e-05]
---------------------------------------------------
user positive negative 42 14 17
u,vi,vj [0.99612504, 0.9257523, 1.1606185]
w1,wu,wy,wa,wv [0.84431714, 0.0, 7.821139e-05, 0.0, 0.0]
Beta [0.99612504, 0.9257523, 1.1606185, 0.84431714, 0.0, 7.821139e-05, 0.0, 0.0, 0.051927567]
alpha list before softmax: [ 4.3869975e-05 -2.5870279e-06 -6.5040367e-06  8.4831045e-06
  7.0112415e-05  1.2701427e-04 -5.4887278e-07 -4.5751967e-06
  3.3661847e-05  1.0371696e-07]
---------------------------------------------------
user positive negative 42 14 85
u,vi,vj [0.98664534, 0.9263949, 0.88798845]
w1,wu,wy

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "C:\Users\NTU\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py", line 3326, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-19-299bbde10e5a>", line 103, in <module>
    image_i:image_1,image_j:image_2})
  File "C:\Users\NTU\Anaconda3\lib\site-packages\tensorflow_core\python\client\session.py", line 956, in run
    run_metadata_ptr)
  File "C:\Users\NTU\Anaconda3\lib\site-packages\tensorflow_core\python\client\session.py", line 1180, in _run
    feed_dict_tensor, options, run_metadata)
  File "C:\Users\NTU\Anaconda3\lib\site-packages\tensorflow_core\python\client\session.py", line 1359, in _do_run
    run_metadata)
  File "C:\Users\NTU\Anaconda3\lib\site-packages\tensorflow_core\python\client\session.py", line 1365, in _do_call
    return fn(*args)
  File "C:\Users\NTU\Anaconda3\lib\site-packages\tensorflow_core\python\client\session.py", line 1350, in _run_fn
    target_list, run_metadata)
  

KeyboardInterrupt: 

In [ ]:
for i in range(len(loss_acc_list)):
    print('Iteration:',i)
    print('loss=',loss_acc_list[i][0])
    print('acc=',loss_acc_list[i][1])
    print('time=',loss_acc_list[i][2])

# Get latent factor and Each weight

In [ ]:
U, Y, A, A1, Au, Ay, Aa, Av,B =sess.run([user_latent, item_latent, aux_item, W1, Wu, Wy, Wa, Wv,Beta])

In [ ]:
print('User latent shape: ',U.shape)
print('photo latent shape: ', Y.shape)
print('Auxilary latent shape: ',A.shape)
print('W1 weight shape: ',A1.shape)
print('Wu weight shape:',Au.shape)
print('Wy weight shape:', Ay.shape)
print('Wa weight shape:',Aa.shape)
print('Wv weight shape:',Av.shape)
print('Beta shape:',B.shape)

In [ ]:
A1

# Testing Part

In [ ]:
result=np.zeros((test_amount,88))
RS=np.zeros((test_amount,88))
#test_idx --> Test 的 index

test_yes_id=[]
for s in range(test_amount):
    print(s,test_idx[s])

    yes=[]
    sample=random.sample(train_t[test_idx[s]],len(train_t[test_idx[s]])) #從training part 的positive feedback 取出YouTuber 當成Auxilary
    #sample=result_yes_id[now]
    test_yes_id.append(sample)
    alpha=np.zeros([len(sample)])
    
    for a in range(len(sample)):
        r =np.max(YouTuber_category[sample[a]]*user_category_norm[test_idx[s]]) #sample a 的category vec *user_category vec
        #print(test_idx[s])
        #print(np.dot(Au[test_idx[s]],np.expand_dims(U[test_idx[s]],0)))
        alpha[a]=np.dot(A1[test_idx[s]],(relu(np.dot(Au,np.expand_dims(U[test_idx[s]],0).T)+np.dot(Ay[sample[a]],np.expand_dims(Y[sample[a]],0).T)+np.dot(Aa,
                            np.expand_dims(A[sample[a]],0).T)+ np.dot(Av,np.expand_dims(all_3374[sample[a]],0).T))))*r
    mul=np.zeros((1,128))
    print('alpha------------',alpha)
    print('softmax alpha--------------',softmax(alpha))
    for i in range(len(sample)):
        mul+=softmax(alpha)[i]*A[sample[i]] #attention alpha*Ai part 
    new_mul=mul+U[test_idx[s]]  #(U+auxilary)
    for k in range(88):
        result[s][k]=np.dot(new_mul,Y[k].T) #(U+auxilary)*photo latent factor
        RS[s][k] = np.dot(new_mul,Y[k].T)+np.dot(B[test_idx[s]], all_3374[k].T)
#print(RS[s])

In [ ]:
#取出test的資料
testRS = np.zeros((test_amount,yt_test_amount)) #shape 150*20
target = np.zeros((test_amount,yt_test_amount))
#test_t 是true的
#test_f 是false的
        
for z in range(test_amount):
    user_id = test_idx[z]
    #positive target YouTuber list
    youtube_t = test_t[z] 
    #not target YouTuber list
    youtube_f = test_f[z]
    
    #前兩個放target的RS
    for i in range(len(youtube_t)):
        testRS[z][i] = RS[z][youtube_t[i]]
        target[z][i] = 1
    for i in range(len(youtube_f)):
        testRS[z][i+len(youtube_t)] = RS[z][youtube_f[i]]

In [ ]:
target

In [ ]:
testRS

In [ ]:
sumtarget = 0
for i in range(len(target)):
    #print(np.sum(target[i]))
    sumtarget += np.sum(target[i])
print('num of positive data in testing:',sumtarget)
print('total testing data:',test_amount*yt_test_amount)

In [ ]:
def topN(sortlist,n):
    topList = []
    for i in range(n):
        topList.append(sortlist.index(max(sortlist)))
        #print(max(sortlist))
        #print(sortlist.index(max(sortlist)))
        sortlist[sortlist.index(max(sortlist))] = -1000000000
    return topList

In [ ]:
count_0_all = []
for i in range(len(testRS)):
    top_0 = topN(list(testRS[i]),int(np.sum(target[i])))
    count_0_all.append(top_0)
    print(top_0)

acc_0 = 0
total = 0
for i in range(len(count_0_all)):
    for j in range(len(count_0_all[i])):
        #print(int(np.sum(target[i])))
        total+=int(np.sum(target[i]))
        if count_0_all[i][j] < int(np.sum(target[i])): #代表是0或1 (也就是target)
            acc_0 += 1
avg_acc = acc_0/100
print('avg_accuarcy for count_0:',avg_acc)
print(acc_0)

In [ ]:
acc_0

In [ ]:
total

# Top 1 

In [ ]:
def F1_score(prec,rec):
    f1 = (2*prec*rec)/(prec+rec)
    return f1

In [ ]:
correct = 0
for i in range(len(testRS)):
    top_0 = topN(list(testRS[i]),1) #取一個
    count_0_all.append(top_0)
    print(top_0)
    if top_0[0] < int(np.sum(target[i])):
        correct += 1

In [ ]:
top1_prec = correct/len(testRS)
top1_recall = correct/(sumtarget)
print('prec ',top1_prec,'recall ',top1_recall)

In [ ]:
#f1 score
print('F1_score:',F1_score(top1_prec,top1_recall))

# Top 3

In [ ]:
correct = 0
for i in range(len(testRS)):
    top_3 = topN(list(testRS[i]),3) #取一個
    count_0_all.append(top_3)
    #print(top_3)
    for j in range(len(top_3)):
        if top_3[j] < int(np.sum(target[i])):
            correct += 1

In [ ]:
top3_prec = correct/(len(testRS)*3)
top3_recall = correct/(sumtarget)
print('prec ',top3_prec,'recall ',top3_recall)

In [ ]:
#f1 score
print('F1_score:',F1_score(top3_prec,top3_recall))

# Top 5

In [ ]:
correct = 0
for i in range(len(testRS)):
    top_5 = topN(list(testRS[i]),5) #取一個
    count_0_all.append(top_5)
    #print(top_5)
    for j in range(len(top_5)):
        if top_5[j] < int(np.sum(target[i])):
            correct += 1

In [ ]:
top5_prec = correct/(len(testRS)*5)
top5_recall = correct/(sumtarget)
print('prec ',top5_prec,'recall ',top5_recall)

In [ ]:
#f1 score
print('F1_score:',F1_score(top5_prec,top5_recall))

In [ ]:
#User_latent_factor = loaddata['User']
#YouTuber_latent_factor = loaddata['YouTuber']

In [ ]:
np.savez('../Data/latent_factor/YRM_up10_ALL/Final/1226.npz', User=U, YouTuber=Y)

In [ ]:
def softmax(x):
    x = x - np.max(x)
    exp_x = np.exp(x)
    softmax_x = exp_x / np.sum(exp_x)
    return softmax_x

In [ ]:
softmax([-0.000000000000000000000000000000000000001,0.00000000000000000000000000000000000001])